In [8]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [2]:
self = DailyPreprocessor()
self.load_data()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


In [3]:
self.main()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
2. 중간산출물을 생성합니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:13<00:00, 1281.32it/s]


2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.
2-3. 직진 및 좌회전(G)을 배정했습니다.
2-2. node2num_cycles.json를 저장했습니다.
3. 이슈사항을 저장합니다.


In [7]:
self.make_match1()

이동류정보 불러오는 중: 100%|██████████| 17280/17280 [01:00<00:00, 286.13it/s]


In [8]:
self.make_match2()
self.make_match3()
self.make_match4()
display(self.match3.head())
display(self.match4.head())

inter_no  phase_no ring_type  move_no inc_dir out_dir
0       175         1         A        8       남       북
1       175         1         B        4       북       남
2       175         2         A        7       북       동
3       175         2         B        3       남       서
4       175         3         A        6       동       서

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle
0       175         1         A        8       남       북       179       004
1       175         1         B        4       북       남       003       176
2       175         2         A        7       북       동       001       095
3       175         2         B        3       남       서       179       270
4       175         3         A        6       동       서       090       270

In [7]:
self.angle_new.angle_code

0     090180
1     270090
2     179270
3     001180
4     270000
5     090270
6     001090
7     179000
8     180270
9     359180
10    270356
11    180356
12    090180
13    268090
14    179270
15    000180
16    268000
17    090270
18    000090
19    179000
20    090180
21    270090
22    180270
23    000180
24    270000
25    090270
26    000090
27    180000
28    090180
29    270090
30    180270
31    000180
32    270000
33    090270
34    000090
35    180000
36    270090
37    090270
38    000180
39    180000
40    090180
41    270090
42    180270
43    000180
44    270000
45    090270
46    000090
47    180000
Name: angle_code, dtype: object

In [26]:
# helper dictionaries
im2inc_angle = dict() # a dictionary that maps (inter_no, move_no) to inc_angle
im2out_angle = dict() # a dictionary that maps (inter_no, move_no) to out_angle
for row in self.angle_new.itertuples():
    inter_no = row.inter_no
    move_no = row.move_no
    angle_code = row.angle_code
    im2inc_angle[(inter_no, move_no)] = angle_code[:3]
    im2out_angle[(inter_no, move_no)] = angle_code[3:]
for inter_no in self.inter_nos:
    im2inc_angle[(inter_no, 17)] = np.nan
    im2out_angle[(inter_no, 17)] = np.nan
    im2inc_angle[(inter_no, 18)] = np.nan
    im2out_angle[(inter_no, 18)] = np.nan

# 진입, 진출 방위각 매칭
self.match4 = self.match3.copy()
for i, row in self.match4.iterrows():
    inter_no = row.inter_no
    move_no = row.move_no
    self.match4.at[i, 'inc_angle'] = im2inc_angle[(inter_no, move_no)]
    self.match4.at[i, 'out_angle'] = im2inc_angle[(inter_no, move_no)]
self.match4.head()

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle
0       175         1         A        8       남       북       179       179
1       175         1         B        4       북       남       001       001
2       175         2         A        7       북       동       001       001
3       175         2         B        3       남       서       179       179
4       175         3         A        6       동       서       090       090

In [14]:
self.angle_new.head()

inter_no  move_no angle_code
0       175        1     090180
1       175        2     270090
2       175        3     179270
3       175        4     001180
4       175        5     270000

array(['090180', '270090', '179270', '001180', '270000', '090270',
       '001090', '179000', '180270', '359180', '270356', '180356',
       '090180', '268090', '179270', '000180', '268000', '090270',
       '000090', '179000', '090180', '270090', '180270', '000180',
       '270000', '090270', '000090', '180000', '090180', '270090',
       '180270', '000180', '270000', '090270', '000090', '180000',
       '270090', '090270', '000180', '180000', '090180', '270090',
       '180270', '000180', '270000', '090270', '000090', '180000'],
      dtype=object)

In [33]:
angle_codes = np.array(self.angle_new.angle_code)
of_length_6 = [len(code)==6 for code in angle_codes]
if not all(of_length_6):
    msg = f"1-4-3-2. 여섯자리가 아닌 각도코드가 존재합니다."
    self.issues.append(msg)
angle_codes = [[code[:3],code[3:]] for code in angle_codes]
angle_codes = [int(item) for sublist in angle_codes for item in sublist]
angle_codes = [0<=code<360 for code in angle_codes]
if not all(angle_codes):
    msg = f"1-4-3-2. 0과 359 사이의 값을 벗어나는 방위각이 존재합니다."
    self.issues.append(msg)


In [5]:
self = DailyPreprocessor()
self.main()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
2. 중간산출물을 생성합니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:17<00:00, 992.30it/s] 


2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.
2-3. 직진 및 좌회전(G)을 배정했습니다.
2-2. node2num_cycles.json를 저장했습니다.
3. 이슈사항을 저장합니다.


In [8]:
display(self.match1.head())
display(self.match2.head())
display(self.match3.head())
display(self.match4.head())
display(self.match5.head())
display(self.match6.head())
display(self.matching.head())

inter_no  phas_A  phas_B  move_A  move_B
0       175       1       1       8       4
1       175       2       2       7       3
2       175       3       3       6       1
3       175       3       4       6       2
4       175       4       4       5       2

inter_no  phase_no ring_type  move_no
0       175         1         A        8
0       175         1         B        4
1       175         2         A        7
1       175         2         B        3
2       175         3         A        6

inter_no  phase_no ring_type  move_no inc_dir out_dir
0       175         1         A        8       남       북
1       175         1         B        4       북       남
2       175         2         A        7       북       동
3       175         2         B        3       남       서
4       175         3         A        6       동       서

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle
0       175         1         A        8       남       북       179       004
1       175         1         B        4       북       남       003       176
2       175         2         A        7       북       동       001       095
3       175         2         B        3       남       서       179       270
4       175         3         A        6       동       서       090       270

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle  \
0       175         1         A        8       남       북       179       004   
1       175         1         B        4       북       남       003       176   
2       175         2         A        7       북       동       001       095   
3       175         2         B        3       남       서       179       270   
4       175         3         A        6       동       서       090       270   

        inc_edge      out_edge node_id  
0  -571542797_02  571500487_01      i0  
1  -571500487_01  571542797_02      i0  
2  -571500487_01  571545870_01      i0  
3  -571542797_02  571510153_01      i0  
4   571545870_02  571510153_01      i0

inter_no node_id  phase_no ring_type  move_no              state
0       175      i0         1         A        8  grrrgrrrgGGGGrgrr
1       175      i0         1         B        4  gGGrgrrrgrrrrrgrr
2       175      i0         2         A        7  grrGgrrrgrrrrrgrr
3       175      i0         2         B        3  grrrgrrrgrrrrGgrr
4       175      i0         3         A        6  grrrgGGrgrrrrrgrr

inter_no node_id  move_no              state
0       175      i0        1  grrrgrrGgrrrrrgrr
1       175      i0        2  grrrgrrrgrrrrrgGr
2       175      i0        3  grrrgrrrgrrrrGgrr
3       175      i0        4  gGGrgrrrgrrrrrgrr
4       175      i0        5  grrrgrrrgrrrrrgrG

줄임말 목록
- `f_` : 진입, from
- `t_` : 진출, to
- `vect` : 방향벡터, unit vector (`np.array([0.6, 0.8])`)
- `rvec` : 방위, direction (동, 서, 남, 북, 북동, 북서, 남동, 남서)
- `dire` : 정방향 방향벡터, unit vector to the right direction (`np.array([0,1])`)

필요한 객체들 목록

- `i2dire2rvec` : `inter_no` $\mapsto$ `dire2rvec`
  - `dire2rvec` : `dire` $\mapsto$ `rvec`
- `i2f` : `inter_no` $\mapsto$ `f_edges`
- `i2t` : `inter_no` $\mapsto$ `t_edges`
- `i2f2dire` : `inter_no` $\mapsto$ `f21dire`
  - `f2dire` : `from_edge` $\mapsto$ `dire`
- `i2t2dire` : `inter_no` $\mapsto$ `t21dire`
  - `t2dire` : `to_edge` $\mapsto$ `dire`